In [1]:
import requests
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
from bs4 import BeautifulSoup as BS
from lxml import html
import re
import difflib
from functools import partial
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 500)
pd.set_option('display.width', 1000)

In [2]:
pip install fuzzywuzzy

Note: you may need to restart the kernel to use updated packages.


In [3]:
from fuzzywuzzy import fuzz
from fuzzywuzzy import process

C:\Users\rober\anaconda3\lib\site-packages\fuzzywuzzy\fuzz.py:11: UserWarning: Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning
  warnings.warn('Using slow pure-python SequenceMatcher. Install python-Levenshtein to remove this warning')


In [4]:
imdbdf = pd.read_csv("../data/imdbdf.csv")

In [5]:
imdbdf = imdbdf.drop("Unnamed: 0",axis=1)

In [6]:
imdbdf.loc[(imdbdf['Title'] == 'SMILE')]

Title  Release Year     Rating  Runtime IMDB Score     Metascore
3     SMILE        2022.0          R    115.0        6.6            68
1006  SMILE        2009.0  Not Rated     84.0        3.3  NO METASCORE
1698  SMILE        2022.0  NO RATING      NaN        3.8  NO METASCORE

In [7]:
imdbdf = imdbdf.drop(1698)

In [8]:
imdbdf.loc[(imdbdf['Title'] == 'SMILE')]

Title  Release Year     Rating  Runtime IMDB Score     Metascore
3     SMILE        2022.0          R    115.0        6.6            68
1006  SMILE        2009.0  Not Rated     84.0        3.3  NO METASCORE

In [9]:
imdbdf['Release Year'] = pd.to_numeric(imdbdf['Release Year'])
imdbdf.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 9999 entries, 0 to 9999
Data columns (total 6 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   Title         9999 non-null   object 
 1   Release Year  9607 non-null   float64
 2   Rating        9999 non-null   object 
 3   Runtime       9234 non-null   float64
 4   IMDB Score    9999 non-null   object 
 5   Metascore     9999 non-null   object 
dtypes: float64(2), object(4)
memory usage: 546.8+ KB


In [10]:
imdbdf = imdbdf[imdbdf['Release Year'].notna()]

In [11]:
imdbdf.index = np.arange(1, len(imdbdf) + 1)
imdbdf['Title'] = imdbdf['Title'].str.upper()

In [12]:
imdbdf['Title'] = imdbdf['Title'].fillna(value=1408)

In [13]:
imdbdf.head(300)

Title  Release Year     Rating  Runtime      IMDB Score     Metascore
1                                             THE MENU        2022.0          R    107.0             7.5            71
2                                                    X        2022.0          R    105.0             6.6            79
3                                        BONES AND ALL        2022.0          R    131.0             7.3            74
4                                                SMILE        2022.0          R    115.0             6.6            68
5                                            BARBARIAN        2022.0          R    102.0             7.1            78
6                                              BHEDIYA        2022.0  NO RATING    156.0             7.7  NO METASCORE
7                                                 NOPE        2022.0          R    130.0             6.9            77
8                                         THE MEAN ONE        2022.0  NO RATING     93.0             6.3            32
9                                          TERRIFIER 2        2022.0  Not Rated    138.0             6.3            59
10                                               PEARL        2022.0          R    103.0             7.0            73
11                                              SCREAM        2022.0          R    114.0             6.3            60
12                                         WHITE NOISE        2022.0          R    136.0             6.6            67
13                               SOMETHING IN THE DIRT        2022.0          R    116.0             6.0            76
14                        THE BABYSITTER: KILLER QUEEN        2020.0      TV-MA    101.0             5.8            22
15                                         SKINAMARINK        2022.0  NO RATING    100.0             5.5  NO METASCORE
16                                   THE ADDAMS FAMILY        2019.0         PG     86.0             5.8            46
17                                           TERRIFIER        2016.0    Unrated     85.0             5.6  NO METASCORE
18                    WINNIE-THE-POOH: BLOOD AND HONEY        2023.0  NO RATING      NaN  NO IMDB RATING  NO METASCORE
19                                           MIDSOMMAR        2019.0          R    148.0             7.1            72
20                                            SCREAM 6        2023.0  NO RATING      NaN  NO IMDB RATING  NO METASCORE
21                                     AMERICAN PSYCHO        2000.0          R    102.0             7.6            64
22                                BODIES BODIES BODIES        2022.0          R     94.0             6.3            69
23                                             GET OUT        2017.0          R    104.0             7.7            85
24         DOCTOR STRANGE IN THE MULTIVERSE OF MADNESS        2022.0      PG-13    126.0             6.9            60
25                                                TUSK        2014.0          R    102.0             5.3            55
26                                  LAST NIGHT IN SOHO        2021.0          R    116.0             7.1            65
27                                     THE BLACK PHONE        2021.0          R    103.0             6.9            65
28                                                PREY        2022.0          R    100.0             7.2            71
29                                  KNOCK AT THE CABIN        2023.0          R      NaN  NO IMDB RATING  NO METASCORE
30                                             KRAMPUS        2015.0      PG-13     98.0             6.2            49
31                                               ALIEN        1979.0          R    117.0             8.5            89
32                                CRIMES OF THE FUTURE        2022.0          R    107.0             5.9            67
33                                             MORBIUS        2022.0      PG-13    104.0             5.2            35
34 

In [14]:
wwbo = pd.read_excel("../data/thenumbers.xlsx", sheet_name=('All Time Worldwide Box Office'))
wwbo.index = np.arange(1, len(wwbo) + 1)
wwbo = wwbo.rename(columns={'Movie' : 'Title', 'Released' : 'Release Year'})
wwbo['Worldwide']=wwbo['Worldwide'].apply('{:,}'.format)
wwbo['Domestic']=wwbo['Domestic'].apply('{:,}'.format)
wwbo['International']=wwbo['International'].apply('{:,}'.format)

In [15]:
wwbo['Title'] = wwbo['Title'].str.upper()

In [16]:
wwbo

Release Year                                 Title    Worldwide       Domestic  International
1             2017                                    IT  701,012,746  328,828,874.0  372,183,872.0
2             1975                                  JAWS  482,947,378  272,257,035.0  210,690,343.0
3             2007                           I AM LEGEND  585,532,684  256,393,010.0  329,139,674.0
4             1973                          THE EXORCIST  428,214,478  230,347,346.0  197,867,132.0
5             2019                       IT: CHAPTER TWO  467,563,955  211,593,228.0  255,970,727.0
...            ...                                   ...          ...            ...            ...
1851          2018                          MANIAC TALES          155            nan          155.0
1852          1933                     THE INVISIBLE MAN          132            nan          132.0
1853          2016                  CAPTURE KILL RELEASE           72            nan           72.0
1854          2021                SLUMBER PARTY MASSACRE           28            nan           28.0
1855          2019  ANTRUM: THE DEADLIEST FILM EVER MADE           26            nan           26.0

[1855 rows x 5 columns]

In [17]:
#df[['a', 'b']] = df[['a','b']].fillna(value=0)

wwbo['Title'] = wwbo['Title'].fillna(value=1408)

In [18]:
wwbo.head(100)

Release Year                                     Title    Worldwide       Domestic  International
1            2017                                        IT  701,012,746  328,828,874.0  372,183,872.0
2            1975                                      JAWS  482,947,378  272,257,035.0  210,690,343.0
3            2007                               I AM LEGEND  585,532,684  256,393,010.0  329,139,674.0
4            1973                              THE EXORCIST  428,214,478  230,347,346.0  197,867,132.0
5            2019                           IT: CHAPTER TWO  467,563,955  211,593,228.0  255,970,727.0
6            2018                             A QUIET PLACE  334,876,670  188,024,361.0  146,852,309.0
7            2017                                   GET OUT  252,297,405  175,837,935.0   76,459,470.0
8            2001                                  HANNIBAL  350,100,280  165,092,266.0  185,008,014.0
9            2021                    A QUIET PLACE: PART II  296,650,356  160,215,764.0  136,434,592.0
10           2018                                 HALLOWEEN  255,416,089  159,366,015.0   96,050,074.0
11           1999                   THE BLAIR WITCH PROJECT  248,300,000  140,539,099.0  107,760,901.0
12           2017                                     SPLIT  278,754,594  138,141,585.0  140,613,009.0
13           2013                             THE CONJURING  317,740,900  137,400,141.0  180,340,759.0
14           1991                  THE SILENCE OF THE LAMBS  275,726,716  130,726,716.0  145,000,000.0
15           2002                                  THE RING  248,218,486  129,094,024.0  119,124,462.0
16           2022                                      NOPE  171,416,477  123,277,080.0   48,139,397.0
17           2018                                   THE NUN  363,391,647  117,450,119.0  245,941,528.0
18           2004                                THE GRUDGE  187,281,115  110,359,362.0   76,921,753.0
19           2009                       PARANORMAL ACTIVITY  194,183,034  107,918,810.0   86,264,224.0
20           2022                                     SMILE  215,978,513  105,778,513.0  110,200,000.0
21           1994                INTERVIEW WITH THE VAMPIRE  223,564,608  105,264,608.0  118,300,000.0
22           2011                     PARANORMAL ACTIVITY 3  207,039,844  104,028,807.0  103,011,037.0
23           1996                                    SCREAM  173,046,640  103,046,663.0   69,999,977.0
24           1978                                    JAWS 2  208,900,376  102,922,376.0  105,978,000.0
25           2016  THE CONJURING 2: THE ENFIELD POLTERGEIST  310,196,332  102,470,008.0  207,726,324.0
26           2017                       ANNABELLE: CREATION  305,384,865  102,092,201.0  203,292,664.0
27           1997                                  SCREAM 2  172,363,301  101,363,301.0   71,000,000.0
28           1999                             SLEEPY HOLLOW  207,068,340  101,068,340.0  106,000,000.0
29           2001                                THE OTHERS  207,765,056   96,522,687.0  111,242,369.0
30           2021                           HALLOWEEN KILLS  130,851,162   92,002,155.0   38,849,007.0
31           1999                              THE HAUNTING  180,188,905   91,188,905.0   89,000,000.0
32           2022                           THE BLACK PHONE  161,204,799   89,887,230.0   71,317,569.0
33           2016                             DON’T BREATHE  158,906,350   89,217,875.0   69,688,475.0
34           2000                                  SCREAM 3  161,838,076   89,138,076.0   72,700,000.0
35           2005                                    SAW II  152,925,093   87,025,093.0   65,900,000.0
36           1979                     THE AMITYVILLE HORROR   86,432,520   86,432,520.0            nan
37           2010                     PARANORMAL ACTIVITY 2  177,512,032   84,752,907.0   92,759,125.0
38           2014                                 ANNABELLE  256,857,527   84,273,813.0  17

In [19]:
tdbo = pd.read_excel("../data/thenumbers.xlsx", sheet_name=('Top 100 Domestic Box Office'))
tdbo.index = np.arange(1, len(tdbo) + 1)
tdbo = tdbo.rename(columns={'Movie' : 'Title', 'Released' : 'Release Year', 'Infl. Adj. Dom.' : 'Domestic - Adjusted for Inflation'})
tdbo['Domestic']=tdbo['Domestic'].apply('{:,}'.format)
tdbo['Domestic - Adjusted for Inflation']=tdbo['Domestic - Adjusted for Inflation'].apply('{:,}'.format)
tdbo['Title'] = tdbo['Title'].str.upper()

In [20]:
tdbo['Title'] = tdbo['Title'].fillna(value=1408)

In [21]:
tdbo

Release Year                                              Title     Domestic Domestic - Adjusted for Inflation
1            2017                                                 IT  328,828,874                       334,783,459
2            1973                                       THE EXORCIST  230,347,346                     1,063,304,892
3            2019                                     IT CHAPTER TWO  211,593,228                       211,824,221
4            2018                                      A QUIET PLACE  188,024,361                       189,262,720
5            2017                                            GET OUT  175,837,935                       179,752,944
6            2020                              A QUIET PLACE PART II  160,215,764                       160,215,764
7            2018                                          HALLOWEEN  159,366,015                       160,409,948
8            1999                            THE BLAIR WITCH PROJECT  140,539,099                       253,689,664
9            2016                                              SPLIT  138,141,585                       141,221,659
10           2013                                      THE CONJURING  137,400,141                       154,976,540
11           2002                                           THE RING  129,094,024                       203,643,481
12           2022                                               NOPE  123,277,080                       123,277,080
13           2018                                            THE NUN  117,450,119                       118,223,666
14           2004                                         THE GRUDGE  110,359,362                       162,962,207
15           2007                                PARANORMAL ACTIVITY  107,918,810                       131,944,856
16           2022                                              SMILE  105,778,513                       105,778,513
17           1994  INTERVIEW WITH THE VAMPIRE: THE VAMPIRE CHRONI...  105,264,608                       235,963,201
18           2011                              PARANORMAL ACTIVITY 3  104,028,807                       120,295,508
19           1996                                             SCREAM  103,046,663                       208,875,525
20           2016                                    THE CONJURING 2  102,470,008                       108,630,057
21           2017                                ANNABELLE: CREATION  102,092,201                       104,368,502
22           1997                                           SCREAM 2  101,363,301                       201,830,911
23           1999                                      SLEEPY HOLLOW  101,068,340                       181,585,991
24           2001                                         THE OTHERS   96,522,687                       156,380,393
25           2021                                    HALLOWEEN KILLS   92,002,155                        92,002,155
26           1999                                       THE HAUNTING   91,188,905                       164,606,736
27           2021                                    THE BLACK PHONE   89,887,230                        89,887,230
28           2016                                      DON'T BREATHE   89,217,875                        94,581,260
29           2000                                           SCREAM 3   89,138,076                       151,650,489
30           2005                                             SAW II   87,025,093                       124,495,771
31           1979                              THE AMITYVILLE HORROR   86,432,520                       315,771,389
32           2010                              PARANORMAL ACTIVITY 2   84,752,907                        98,501,884
33           2014                                          ANNABELLE   84,273,813                        94,588,843
34           2013                               INSIDIOUS: CH

In [22]:
top100comb = pd.merge(tdbo, imdbdf, left_on = ['Title', 'Release Year'], right_on = ['Title', 'Release Year'], how='left')
top100comb.index = np.arange(1, len(top100comb) + 1)

In [23]:
top100comb

Release Year                                              Title     Domestic Domestic - Adjusted for Inflation Rating  Runtime IMDB Score     Metascore
1            2017                                                 IT  328,828,874                       334,783,459      R    135.0        7.3            69
2            1973                                       THE EXORCIST  230,347,346                     1,063,304,892      R    122.0        8.1            81
3            2019                                     IT CHAPTER TWO  211,593,228                       211,824,221      R    169.0        6.5            58
4            2018                                      A QUIET PLACE  188,024,361                       189,262,720  PG-13     90.0        7.5            82
5            2017                                            GET OUT  175,837,935                       179,752,944      R    104.0        7.7            85
6            2020                              A QUIET PLACE PART II  160,215,764                       160,215,764  PG-13     97.0        7.2            71
7            2018                                          HALLOWEEN  159,366,015                       160,409,948      R    106.0        6.5            67
8            1999                            THE BLAIR WITCH PROJECT  140,539,099                       253,689,664      R     81.0        6.5            81
9            2016                                              SPLIT  138,141,585                       141,221,659  PG-13    117.0        7.3            62
10           2013                                      THE CONJURING  137,400,141                       154,976,540      R    112.0        7.5            68
11           2002                                           THE RING  129,094,024                       203,643,481  PG-13    115.0        7.1            57
12           2022                                               NOPE  123,277,080                       123,277,080      R    130.0        6.9            77
13           2018                                            THE NUN  117,450,119                       118,223,666      R     96.0        5.3            46
14           2004                                         THE GRUDGE  110,359,362                       162,962,207  PG-13     91.0        5.9            49
15           2007                                PARANORMAL ACTIVITY  107,918,810                       131,944,856      R     86.0        6.3            68
16           2022                                              SMILE  105,778,513                       105,778,513      R    115.0        6.6            68
17           1994  INTERVIEW WITH THE VAMPIRE: THE VAMPIRE CHRONI...  105,264,608                       235,963,201      R    123.0        7.5            59
18           2011                              PARANORMAL ACTIVITY 3  104,028,807                       120,295,508      R     83.0        5.8            59
19           1996                                             SCREAM  103,046,663                       208,875,525      R    111.0        7.4            65
20           2016                                    THE CONJURING 2  102,470,008                       108,630,057      R    134.0        7.3            65
21           2017                                ANNABELLE: CREATION  102,092,201                       104,368,502      R    109.0        6.5            62
22           1997                                           SCREAM 2  101,363,301                       201,830,911      R    120.0        6.3            63
23           1999                                      SLEEPY HOLLOW  101,068,340                       181,585,991      R    105.0        7.3            65
24           2001                                         THE OTHERS   96,522,687                       156,380,393  PG-13    104.0        7.6            74
25           2021                                    HALLOWEEN KILLS   92,002,15

In [25]:
imdbdf['Release Year'] = imdbdf['Release Year'].astype(str)

In [26]:
imdbdf.dtypes

Title            object
Release Year     object
Rating           object
Runtime         float64
IMDB Score       object
Metascore        object
dtype: object

In [27]:
imdbdf['Title and Year'] = imdbdf['Title'] + " " + imdbdf['Release Year']

In [28]:
imdbdf.head()

Title Release Year Rating  Runtime IMDB Score Metascore        Title and Year
1       THE MENU       2022.0      R    107.0        7.5        71       THE MENU 2022.0
2              X       2022.0      R    105.0        6.6        79              X 2022.0
3  BONES AND ALL       2022.0      R    131.0        7.3        74  BONES AND ALL 2022.0
4          SMILE       2022.0      R    115.0        6.6        68          SMILE 2022.0
5      BARBARIAN       2022.0      R    102.0        7.1        78      BARBARIAN 2022.0

In [29]:
wwbo['Release Year'] = wwbo['Release Year'].astype(str)

In [30]:
wwbo['Title'] = wwbo['Title'].astype(str)

In [31]:
wwbo['Title and Year'] = wwbo['Title'] + " " + wwbo['Release Year']

In [32]:
wwbo

Release Year                                 Title    Worldwide       Domestic  International                             Title and Year
1            2017                                    IT  701,012,746  328,828,874.0  372,183,872.0                                    IT 2017
2            1975                                  JAWS  482,947,378  272,257,035.0  210,690,343.0                                  JAWS 1975
3            2007                           I AM LEGEND  585,532,684  256,393,010.0  329,139,674.0                           I AM LEGEND 2007
4            1973                          THE EXORCIST  428,214,478  230,347,346.0  197,867,132.0                          THE EXORCIST 1973
5            2019                       IT: CHAPTER TWO  467,563,955  211,593,228.0  255,970,727.0                       IT: CHAPTER TWO 2019
...           ...                                   ...          ...            ...            ...                                        ...
1851         2018                          MANIAC TALES          155            nan          155.0                          MANIAC TALES 2018
1852         1933                     THE INVISIBLE MAN          132            nan          132.0                     THE INVISIBLE MAN 1933
1853         2016                  CAPTURE KILL RELEASE           72            nan           72.0                  CAPTURE KILL RELEASE 2016
1854         2021                SLUMBER PARTY MASSACRE           28            nan           28.0                SLUMBER PARTY MASSACRE 2021
1855         2019  ANTRUM: THE DEADLIEST FILM EVER MADE           26            nan           26.0  ANTRUM: THE DEADLIEST FILM EVER MADE 2019

[1855 rows x 6 columns]

In [33]:
wwbo.dtypes

Release Year      object
Title             object
Worldwide         object
Domestic          object
International     object
Title and Year    object
dtype: object

In [34]:
wwbo

Release Year                                 Title    Worldwide       Domestic  International                             Title and Year
1            2017                                    IT  701,012,746  328,828,874.0  372,183,872.0                                    IT 2017
2            1975                                  JAWS  482,947,378  272,257,035.0  210,690,343.0                                  JAWS 1975
3            2007                           I AM LEGEND  585,532,684  256,393,010.0  329,139,674.0                           I AM LEGEND 2007
4            1973                          THE EXORCIST  428,214,478  230,347,346.0  197,867,132.0                          THE EXORCIST 1973
5            2019                       IT: CHAPTER TWO  467,563,955  211,593,228.0  255,970,727.0                       IT: CHAPTER TWO 2019
...           ...                                   ...          ...            ...            ...                                        ...
1851         2018                          MANIAC TALES          155            nan          155.0                          MANIAC TALES 2018
1852         1933                     THE INVISIBLE MAN          132            nan          132.0                     THE INVISIBLE MAN 1933
1853         2016                  CAPTURE KILL RELEASE           72            nan           72.0                  CAPTURE KILL RELEASE 2016
1854         2021                SLUMBER PARTY MASSACRE           28            nan           28.0                SLUMBER PARTY MASSACRE 2021
1855         2019  ANTRUM: THE DEADLIEST FILM EVER MADE           26            nan           26.0  ANTRUM: THE DEADLIEST FILM EVER MADE 2019

[1855 rows x 6 columns]

In [35]:
wwbo.to_csv('wwbo.csv')

In [36]:
imdbdf.dtypes

Title              object
Release Year       object
Rating             object
Runtime           float64
IMDB Score         object
Metascore          object
Title and Year     object
dtype: object

In [37]:
imdbdf['Runtime'] = imdbdf['Runtime'].astype(str)

In [38]:
imdbdf

Title Release Year     Rating Runtime      IMDB Score     Metascore                     Title and Year
1                       THE MENU       2022.0          R   107.0             7.5            71                    THE MENU 2022.0
2                              X       2022.0          R   105.0             6.6            79                           X 2022.0
3                  BONES AND ALL       2022.0          R   131.0             7.3            74               BONES AND ALL 2022.0
4                          SMILE       2022.0          R   115.0             6.6            68                       SMILE 2022.0
5                      BARBARIAN       2022.0          R   102.0             7.1            78                   BARBARIAN 2022.0
...                          ...          ...        ...     ...             ...           ...                                ...
9603       WALKING DEAD - TOMATE       2022.0  NO RATING    79.0             3.6  NO METASCORE       WALKING DEAD - TOMATE 2022.0
9604                   MANNEQUIN       2023.0  NO RATING     nan  NO IMDB RATING  NO METASCORE                   MANNEQUIN 2023.0
9605  UNDEAD OR ALIVE: A ZOMBEDY       2007.0          R    91.0             5.1  NO METASCORE  UNDEAD OR ALIVE: A ZOMBEDY 2007.0
9606               SECOND ORIGIN       2015.0  NO RATING   106.0             4.5  NO METASCORE               SECOND ORIGIN 2015.0
9607                       BETSY       2018.0  NO RATING    81.0             3.1  NO METASCORE                       BETSY 2018.0

[9607 rows x 7 columns]

In [40]:
imdbdf.loc[(imdbdf['Title'] == '1408')]

Title Release Year Rating Runtime IMDB Score Metascore Title and Year
325  1408       2007.0  PG-13   104.0        6.8        64    1408 2007.0

In [41]:
wwbo.loc[(wwbo['Title'] == '1408')]

Release Year Title    Worldwide      Domestic International Title and Year
55           2007  1408  131,263,370  71,985,628.0  59,277,742.0      1408 2007
594          2016  1408      922,727     779,820.0     142,907.0      1408 2016
744          2011  1408    2,756,875      38,100.0   2,718,775.0      1408 2011
959          2018  1408    3,130,260           nan   3,130,260.0      1408 2018
1347         2020  1408      123,784           nan     123,784.0      1408 2020

In [42]:
#imdbdf = imdbdf.drop(1698) drop extra 1408

In [43]:
wwbo = wwbo.drop(594)
wwbo = wwbo.drop(744)
wwbo = wwbo.drop(959)
wwbo = wwbo.drop(1347)

In [44]:
wwbo.loc[(wwbo['Title'] == '1408')]

Release Year Title    Worldwide      Domestic International Title and Year
55         2007  1408  131,263,370  71,985,628.0  59,277,742.0      1408 2007

In [45]:
wwbo.head()

Release Year            Title    Worldwide       Domestic  International        Title and Year
1         2017               IT  701,012,746  328,828,874.0  372,183,872.0               IT 2017
2         1975             JAWS  482,947,378  272,257,035.0  210,690,343.0             JAWS 1975
3         2007      I AM LEGEND  585,532,684  256,393,010.0  329,139,674.0      I AM LEGEND 2007
4         1973     THE EXORCIST  428,214,478  230,347,346.0  197,867,132.0     THE EXORCIST 1973
5         2019  IT: CHAPTER TWO  467,563,955  211,593,228.0  255,970,727.0  IT: CHAPTER TWO 2019

In [46]:
wwbo.shape

(1851, 6)

In [47]:
imdbdf.head()

Title Release Year Rating Runtime IMDB Score Metascore        Title and Year
1       THE MENU       2022.0      R   107.0        7.5        71       THE MENU 2022.0
2              X       2022.0      R   105.0        6.6        79              X 2022.0
3  BONES AND ALL       2022.0      R   131.0        7.3        74  BONES AND ALL 2022.0
4          SMILE       2022.0      R   115.0        6.6        68          SMILE 2022.0
5      BARBARIAN       2022.0      R   102.0        7.1        78      BARBARIAN 2022.0

In [48]:
imdbdf.shape

(9607, 7)

In [49]:
# title a / title b / calc ratio of similarity - abi's suggestion

#df['candidate'] = get_close_matches()

In [50]:
# worldwidecomb = pd.merge(imdbdf, wwbo, left_on = ['Title', 'Release Year'], right_on = ['Title', 'Release Year'], how='inner')
# worldwidecomb.index = np.arange(1, len(top100comb) + 1)

# df2['team'] = df2['team'].apply(lambda x: difflib.get_close_matches(x, df1['team'])[0])

#wwbo['Title and Year'] = wwbo['Title and Year'].map(lambda x: difflib.get_close_matches(x, imdbdf['Title and Year'])[0])

#test = imdbdf.merge(wwbo)

#df2.index = df2.index.map(lambda x: difflib.get_close_matches(x, df1.index)[0])

# for x in wwbo['Title and Year']:
#     wwbo['Match'] = difflib.get_close_matches(x, imdbdf['Title and Year'])[0]
#     print(x)
#     print(difflib.get_close_matches(x, imdbdf['Title and Year'])[0])

In [51]:
wwbo

Release Year                                 Title    Worldwide       Domestic  International                             Title and Year
1            2017                                    IT  701,012,746  328,828,874.0  372,183,872.0                                    IT 2017
2            1975                                  JAWS  482,947,378  272,257,035.0  210,690,343.0                                  JAWS 1975
3            2007                           I AM LEGEND  585,532,684  256,393,010.0  329,139,674.0                           I AM LEGEND 2007
4            1973                          THE EXORCIST  428,214,478  230,347,346.0  197,867,132.0                          THE EXORCIST 1973
5            2019                       IT: CHAPTER TWO  467,563,955  211,593,228.0  255,970,727.0                       IT: CHAPTER TWO 2019
...           ...                                   ...          ...            ...            ...                                        ...
1851         2018                          MANIAC TALES          155            nan          155.0                          MANIAC TALES 2018
1852         1933                     THE INVISIBLE MAN          132            nan          132.0                     THE INVISIBLE MAN 1933
1853         2016                  CAPTURE KILL RELEASE           72            nan           72.0                  CAPTURE KILL RELEASE 2016
1854         2021                SLUMBER PARTY MASSACRE           28            nan           28.0                SLUMBER PARTY MASSACRE 2021
1855         2019  ANTRUM: THE DEADLIEST FILM EVER MADE           26            nan           26.0  ANTRUM: THE DEADLIEST FILM EVER MADE 2019

[1851 rows x 6 columns]

In [52]:
#df.to_csv('file1.csv')

In [53]:
wwbo.to_csv('wwbo.csv')

In [54]:
imdbdf.to_csv('imdbdf.csv')

In [194]:
wwbo['match'] = wwbo['Title'].str[0:8]

In [195]:
wwbo

Release Year                                              Title    Worldwide       Domestic  International                                     Title and Year     match
1            2017                                                 IT  701,012,746  328,828,874.0  372,183,872.0                                            IT 2017        IT
2            1975                                               JAWS  482,947,378  272,257,035.0  210,690,343.0                                          JAWS 1975      JAWS
3            2007                                        I AM LEGEND  585,532,684  256,393,010.0  329,139,674.0                                   I AM LEGEND 2007  I AM LEG
4            1973                                       THE EXORCIST  428,214,478  230,347,346.0  197,867,132.0                                  THE EXORCIST 1973  THE EXOR
5            2019                                    IT: CHAPTER TWO  467,563,955  211,593,228.0  255,970,727.0                               IT: CHAPTER TWO 2019  IT: CHAP
6            2018                                      A QUIET PLACE  334,876,670  188,024,361.0  146,852,309.0                                 A QUIET PLACE 2018  A QUIET 
7            2017                                            GET OUT  252,297,405  175,837,935.0   76,459,470.0                                       GET OUT 2017   GET OUT
8            2001                                           HANNIBAL  350,100,280  165,092,266.0  185,008,014.0                                      HANNIBAL 2001  HANNIBAL
9            2021                             A QUIET PLACE: PART II  296,650,356  160,215,764.0  136,434,592.0                        A QUIET PLACE: PART II 2021  A QUIET 
10           2018                                          HALLOWEEN  255,416,089  159,366,015.0   96,050,074.0                                     HALLOWEEN 2018  HALLOWEE
11           1999                            THE BLAIR WITCH PROJECT  248,300,000  140,539,099.0  107,760,901.0                       THE BLAIR WITCH PROJECT 1999  THE BLAI
12           2017                                              SPLIT  278,754,594  138,141,585.0  140,613,009.0                                         SPLIT 2017     SPLIT
13           2013                                      THE CONJURING  317,740,900  137,400,141.0  180,340,759.0                                 THE CONJURING 2013  THE CONJ
14           1991                           THE SILENCE OF THE LAMBS  275,726,716  130,726,716.0  145,000,000.0                      THE SILENCE OF THE LAMBS 1991  THE SILE
15           2002                                           THE RING  248,218,486  129,094,024.0  119,124,462.0                                      THE RING 2002  THE RING
16           2022                                               NOPE  171,416,477  123,277,080.0   48,139,397.0                                          NOPE 2022      NOPE
17           2018                                            THE NUN  363,391,647  117,450,119.0  245,941,528.0                                       THE NUN 2018   THE NUN
18           2004                                         THE GRUDGE  187,281,115  110,359,362.0   76,921,753.0                                    THE GRUDGE 2004  THE GRUD
19           2009                                PARANORMAL ACTIVITY  194,183,034  107,918,810.0   86,264,224.0                           PARANORMAL ACTIVITY 2009  PARANORM
20           2022                                              SMILE  215,978,513  105,778,513.0  110,200,000.0                                         SMILE 2022     SMILE
21           1994                         INTERVIEW WITH THE VAMPIRE  223,564,608  105,264,608.0  118,300,000.0                    INTERVIEW WITH THE VAMPIRE 1994  INTERVIE
22           2011                              PARANORMAL ACTIVITY 3  207,039,844  104,028,807.0  103,011,037.0                         PARANORMAL ACTIVITY 3 2011  PARANORM
23           1996         

In [196]:
imdbdf['match'] = imdbdf['Title and Year'].str[0:8]

In [197]:
imdbdf.head()

Title Release Year Rating Runtime IMDB Score Metascore        Title and Year     match
1       THE MENU       2022.0      R   107.0        7.5        71       THE MENU 2022.0  THE MENU
2              X       2022.0      R   105.0        6.6        79              X 2022.0  X 2022.0
3  BONES AND ALL       2022.0      R   131.0        7.3        74  BONES AND ALL 2022.0  BONES AN
4          SMILE       2022.0      R   115.0        6.6        68          SMILE 2022.0  SMILE 20
5      BARBARIAN       2022.0      R   102.0        7.1        78      BARBARIAN 2022.0  BARBARIA

In [198]:
mergedf = pd.merge(imdbdf, wwbo, how='inner', on='match')

In [199]:
mergedf

Title_x Release Year_x     Rating Runtime      IMDB Score     Metascore                                   Title and Year_x     match Release Year_y                                           Title_y    Worldwide       Domestic  International                                   Title and Year_y
0                                             BARBARIAN         2022.0          R   102.0             7.1            78                                   BARBARIAN 2022.0  BARBARIA           2022                                         BARBARIAN   44,734,287   40,842,944.0    3,891,343.0                                     BARBARIAN 2022
1                                            BARBARIANS         2021.0  NO RATING    89.0             4.7            57                                  BARBARIANS 2021.0  BARBARIA           2022                                         BARBARIAN   44,734,287   40,842,944.0    3,891,343.0                                     BARBARIAN 2022
2                                           TERRIFIER 2         2022.0  Not Rated   138.0             6.3            59                                 TERRIFIER 2 2022.0  TERRIFIE           2022                                       TERRIFIER 2   11,287,125   10,640,105.0      647,020.0                                   TERRIFIER 2 2022
3                                             TERRIFIER         2016.0    Unrated    85.0             5.6  NO METASCORE                                   TERRIFIER 2016.0  TERRIFIE           2022                                       TERRIFIER 2   11,287,125   10,640,105.0      647,020.0                                   TERRIFIER 2 2022
4                                             TERRIFIED         2017.0  Not Rated    87.0             6.5  NO METASCORE                                   TERRIFIED 2017.0  TERRIFIE           2022                                       TERRIFIER 2   11,287,125   10,640,105.0      647,020.0                                   TERRIFIER 2 2022
5                                             TERRIFIED         1995.0          R    95.0             3.5  NO METASCORE                                   TERRIFIED 1995.0  TERRIFIE           2022                                       TERRIFIER 2   11,287,125   10,640,105.0      647,020.0                                   TERRIFIER 2 2022
6                                             TERRIFIED         1963.0      TV-14    81.0             4.3  NO METASCORE                                   TERRIFIED 1963.0  TERRIFIE           2022                                       TERRIFIER 2   11,287,125   10,640,105.0      647,020.0                                   TERRIFIER 2 2022
7                                                SCREAM         2022.0          R   114.0             6.3            60                                      SCREAM 2022.0  SCREAM 2           1997                                          SCREAM 2  172,363,301  101,363,301.0   71,000,000.0                                      SCREAM 2 1997
8                                              SCREAM 2         1997.0          R   120.0             6.3            63                                    SCREAM 2 1997.0  SCREAM 2           1997                                          SCREAM 2  172,363,301  101,363,301.0   71,000,000.0                                      SCREAM 2 1997
9                                           WHITE NOISE         2022.0          R   136.0             6.6            67                                 WHITE NOISE 2022.0  WHITE NO           2005                                       WHITE NOISE   92,094,360   56,094,360.0   36,000,000.0                                   WHITE NOISE 2005
10                                          WHITE NOISE         2022.0          R   136.0             6.6            67                                 WHITE NOISE 2022.0  WHITE NO           2008                          WHITE NOISE 2: THE LIGHT    8,243,567            nan    8,243,567.0                    

In [200]:
mergedf['ratio'] = mergedf.apply((lambda x: fuzz.ratio(x['Title and Year_x'], x['Title and Year_y'])), axis=1)

In [201]:
mergedf.head()

Title_x Release Year_x     Rating Runtime IMDB Score     Metascore    Title and Year_x     match Release Year_y      Title_y   Worldwide      Domestic International  Title and Year_y  ratio
0    BARBARIAN         2022.0          R   102.0        7.1            78    BARBARIAN 2022.0  BARBARIA           2022    BARBARIAN  44,734,287  40,842,944.0   3,891,343.0    BARBARIAN 2022     93
1   BARBARIANS         2021.0  NO RATING    89.0        4.7            57   BARBARIANS 2021.0  BARBARIA           2022    BARBARIAN  44,734,287  40,842,944.0   3,891,343.0    BARBARIAN 2022     84
2  TERRIFIER 2         2022.0  Not Rated   138.0        6.3            59  TERRIFIER 2 2022.0  TERRIFIE           2022  TERRIFIER 2  11,287,125  10,640,105.0     647,020.0  TERRIFIER 2 2022     94
3    TERRIFIER         2016.0    Unrated    85.0        5.6  NO METASCORE    TERRIFIER 2016.0  TERRIFIE           2022  TERRIFIER 2  11,287,125  10,640,105.0     647,020.0  TERRIFIER 2 2022     75
4    TERRIFIED         2017.0  Not Rated    87.0        6.5  NO METASCORE    TERRIFIED 2017.0  TERRIFIE           2022  TERRIFIER 2  11,287,125  10,640,105.0     647,020.0  TERRIFIER 2 2022     69

In [202]:
mergedffilter = mergedf.loc[mergedf['ratio'] > 80]

In [203]:
mergedffilter
mergedffilter.index = np.arange(1, len(mergedffilter) + 1)

In [204]:
mergedffilter

Title_x Release Year_x     Rating Runtime      IMDB Score     Metascore                                   Title and Year_x     match Release Year_y                                           Title_y    Worldwide       Domestic  International                                   Title and Year_y  ratio
1                                            BARBARIAN         2022.0          R   102.0             7.1            78                                   BARBARIAN 2022.0  BARBARIA           2022                                         BARBARIAN   44,734,287   40,842,944.0    3,891,343.0                                     BARBARIAN 2022     93
2                                           BARBARIANS         2021.0  NO RATING    89.0             4.7            57                                  BARBARIANS 2021.0  BARBARIA           2022                                         BARBARIAN   44,734,287   40,842,944.0    3,891,343.0                                     BARBARIAN 2022     84
3                                          TERRIFIER 2         2022.0  Not Rated   138.0             6.3            59                                 TERRIFIER 2 2022.0  TERRIFIE           2022                                       TERRIFIER 2   11,287,125   10,640,105.0      647,020.0                                   TERRIFIER 2 2022     94
4                                             SCREAM 2         1997.0          R   120.0             6.3            63                                    SCREAM 2 1997.0  SCREAM 2           1997                                          SCREAM 2  172,363,301  101,363,301.0   71,000,000.0                                      SCREAM 2 1997     93
5                                          WHITE NOISE         2022.0          R   136.0             6.6            67                                 WHITE NOISE 2022.0  WHITE NO           2005                                       WHITE NOISE   92,094,360   56,094,360.0   36,000,000.0                                   WHITE NOISE 2005     88
6                                          WHITE NOISE         2005.0      PG-13   101.0             5.5            30                                 WHITE NOISE 2005.0  WHITE NO           2005                                       WHITE NOISE   92,094,360   56,094,360.0   36,000,000.0                                   WHITE NOISE 2005     94
7                             WHITE NOISE 2: THE LIGHT         2007.0      PG-13    99.0             5.7  NO METASCORE                    WHITE NOISE 2: THE LIGHT 2007.0  WHITE NO           2008                          WHITE NOISE 2: THE LIGHT    8,243,567            nan    8,243,567.0                      WHITE NOISE 2: THE LIGHT 2008     93
8                                SOMETHING IN THE DIRT         2022.0          R   116.0             6.0            76                       SOMETHING IN THE DIRT 2022.0  SOMETHIN           2022                             SOMETHING IN THE DIRT      107,114            nan      107,114.0                         SOMETHING IN THE DIRT 2022     96
9                               SOMETHING IN THE WOODS         2022.0  NO RATING    76.0             2.6  NO METASCORE                      SOMETHING IN THE WOODS 2022.0  SOMETHIN           2022                             SOMETHING IN THE DIRT      107,114            nan      107,114.0                         SOMETHING IN THE DIRT 2022     84
10                                           MIDSOMMAR         2019.0          R   148.0             7.1            72                                   MIDSOMMAR 2019.0  MIDSOMMA           2019                                         MIDSOMMAR   46,757,893   27,426,363.0   19,331,530.0                                     MIDSOMMAR 2019     93
11                                    AMERICAN CARNAGE         2022.0          R   101.0             4.8  NO METASCORE                            AMERICAN CARNAGE 2022.0  AMERICAN           2022                                  AMERICAN CARN

In [205]:
mergedffilter = mergedffilter.drop(['Release Year_x', 'Title and Year_x', 'match', 'Title_y', 'Title and Year_y', 'ratio'], axis=1)

In [206]:
mergedffilter

Title_x     Rating Runtime      IMDB Score     Metascore Release Year_y    Worldwide       Domestic  International
1                                            BARBARIAN          R   102.0             7.1            78           2022   44,734,287   40,842,944.0    3,891,343.0
2                                           BARBARIANS  NO RATING    89.0             4.7            57           2022   44,734,287   40,842,944.0    3,891,343.0
3                                          TERRIFIER 2  Not Rated   138.0             6.3            59           2022   11,287,125   10,640,105.0      647,020.0
4                                             SCREAM 2          R   120.0             6.3            63           1997  172,363,301  101,363,301.0   71,000,000.0
5                                          WHITE NOISE          R   136.0             6.6            67           2005   92,094,360   56,094,360.0   36,000,000.0
6                                          WHITE NOISE      PG-13   101.0             5.5            30           2005   92,094,360   56,094,360.0   36,000,000.0
7                             WHITE NOISE 2: THE LIGHT      PG-13    99.0             5.7  NO METASCORE           2008    8,243,567            nan    8,243,567.0
8                                SOMETHING IN THE DIRT          R   116.0             6.0            76           2022      107,114            nan      107,114.0
9                               SOMETHING IN THE WOODS  NO RATING    76.0             2.6  NO METASCORE           2022      107,114            nan      107,114.0
10                                           MIDSOMMAR          R   148.0             7.1            72           2019   46,757,893   27,426,363.0   19,331,530.0
11                                    AMERICAN CARNAGE          R   101.0             4.8  NO METASCORE           2022       46,389            nan       46,389.0
12                                BODIES BODIES BODIES          R    94.0             6.3            69           2022   13,454,835   11,446,602.0    2,008,233.0
13                                        DOCTOR SLEEP          R   152.0             7.3            59           2019   71,720,838   31,581,712.0   40,139,126.0
14                                     THE BLACK PHONE          R   103.0             6.9            65           2022  161,204,799   89,887,230.0   71,317,569.0
15                            THE BLACKCOAT'S DAUGHTER          R    93.0             5.9            68           2017      143,545       20,435.0      123,110.0
16                                CRIMES OF THE FUTURE          R   107.0             5.9            67           2022    3,600,102    2,452,882.0    1,147,220.0
17                                      THE INVITATION      PG-13   105.0             5.2            45           2022   33,689,288   25,100,080.0    8,589,208.0
18                                   THE INVISIBLE MAN          R   124.0             7.1            72           2020  139,011,965   64,914,050.0   74,097,915.0
19                                      THE INVITATION  Not Rated   100.0             6.6            74           2022   33,689,288   25,100,080.0    8,589,208.0
20                                   THE INVISIBLE MAN      TV-PG    71.0             7.6            87           2020  139,011,965   64,914,050.0   74,097,915.0
21                                   THE INVISIBLE MAN      TV-PG    71.0             7.6            87           1933          132            nan          132.0
22                                THE INVISIBLE MANIAC          R    86.0             4.1  NO METASCORE           2020  139,011,965   64,914,050.0   74,097,915.0
23                                THE INVISIBLE MANIAC          R    86.0             4.1  NO METASCORE           1933          132            nan          132.0
24                                   THE INVISIBLE RAY   Approved    80.0             6.5  NO METASCORE           1933          132            nan          132

In [207]:
cleanmerge = mergedffilter.rename(columns={'Title_x': 'Title', 'Release Year_y': 'Release Year'})

In [208]:
pd.set_option('display.max_rows', None)

In [209]:
cleanmerge

Title     Rating Runtime      IMDB Score     Metascore Release Year    Worldwide       Domestic  International
1                                            BARBARIAN          R   102.0             7.1            78         2022   44,734,287   40,842,944.0    3,891,343.0
2                                           BARBARIANS  NO RATING    89.0             4.7            57         2022   44,734,287   40,842,944.0    3,891,343.0
3                                          TERRIFIER 2  Not Rated   138.0             6.3            59         2022   11,287,125   10,640,105.0      647,020.0
4                                             SCREAM 2          R   120.0             6.3            63         1997  172,363,301  101,363,301.0   71,000,000.0
5                                          WHITE NOISE          R   136.0             6.6            67         2005   92,094,360   56,094,360.0   36,000,000.0
6                                          WHITE NOISE      PG-13   101.0             5.5            30         2005   92,094,360   56,094,360.0   36,000,000.0
7                             WHITE NOISE 2: THE LIGHT      PG-13    99.0             5.7  NO METASCORE         2008    8,243,567            nan    8,243,567.0
8                                SOMETHING IN THE DIRT          R   116.0             6.0            76         2022      107,114            nan      107,114.0
9                               SOMETHING IN THE WOODS  NO RATING    76.0             2.6  NO METASCORE         2022      107,114            nan      107,114.0
10                                           MIDSOMMAR          R   148.0             7.1            72         2019   46,757,893   27,426,363.0   19,331,530.0
11                                    AMERICAN CARNAGE          R   101.0             4.8  NO METASCORE         2022       46,389            nan       46,389.0
12                                BODIES BODIES BODIES          R    94.0             6.3            69         2022   13,454,835   11,446,602.0    2,008,233.0
13                                        DOCTOR SLEEP          R   152.0             7.3            59         2019   71,720,838   31,581,712.0   40,139,126.0
14                                     THE BLACK PHONE          R   103.0             6.9            65         2022  161,204,799   89,887,230.0   71,317,569.0
15                            THE BLACKCOAT'S DAUGHTER          R    93.0             5.9            68         2017      143,545       20,435.0      123,110.0
16                                CRIMES OF THE FUTURE          R   107.0             5.9            67         2022    3,600,102    2,452,882.0    1,147,220.0
17                                      THE INVITATION      PG-13   105.0             5.2            45         2022   33,689,288   25,100,080.0    8,589,208.0
18                                   THE INVISIBLE MAN          R   124.0             7.1            72         2020  139,011,965   64,914,050.0   74,097,915.0
19                                      THE INVITATION  Not Rated   100.0             6.6            74         2022   33,689,288   25,100,080.0    8,589,208.0
20                                   THE INVISIBLE MAN      TV-PG    71.0             7.6            87         2020  139,011,965   64,914,050.0   74,097,915.0
21                                   THE INVISIBLE MAN      TV-PG    71.0             7.6            87         1933          132            nan          132.0
22                                THE INVISIBLE MANIAC          R    86.0             4.1  NO METASCORE         2020  139,011,965   64,914,050.0   74,097,915.0
23                                THE INVISIBLE MANIAC          R    86.0             4.1  NO METASCORE         1933          132            nan          132.0
24                                   THE INVISIBLE RAY   Approved    80.0             6.5  NO METASCORE         1933          132            nan          132.0
25                                         THE SH

In [210]:
duplicateRows = cleanmerge[cleanmerge.duplicated(['Title'])]

In [211]:
len(duplicateRows)

252

In [212]:
cleanmerge = cleanmerge[cleanmerge['Metascore'] != 'NO METASCORE']

MOVIES RANKED BY IMDB SCORE

In [218]:
rankbyimdb = cleanmerge.sort_values(by=['IMDB Score'], ascending=False)
rankbyimdb.index = np.arange(1, len(rankbyimdb) + 1)

In [219]:
rankbyimdb

Title     Rating Runtime IMDB Score Metascore Release Year    Worldwide       Domestic  International
1                                         THE SHINING          R   146.0        8.4        66         1980   45,601,938   44,568,631.0    1,033,307.0
2                                           THE THING          R   109.0        8.2        57         1982   13,841,714   13,782,838.0       58,876.0
3                                        THE EXORCIST          R   122.0        8.1        81         1973  428,214,478  230,347,346.0  197,867,132.0
4                                     ROSEMARY'S BABY   Approved   137.0        8.0        96         1968   33,396,740   33,395,426.0        1,314.0
5                                           KING KONG     Passed   100.0        7.9        90         1933   10,001,781   10,000,000.0        1,781.0
6                                    DAWN OF THE DEAD    Unrated   127.0        7.8        71         2004  103,452,875   58,990,765.0   44,462,110.0
7                                    DAWN OF THE DEAD    Unrated   127.0        7.8        71         1979   55,000,000    5,100,000.0   49,900,000.0
8                                        FRANKENSTEIN     Passed    70.0        7.8        91         1931   12,001,435   12,000,000.0        1,435.0
9                                        FRANKENSTEIN     Passed    70.0        7.8        91         1994  112,006,296   22,006,296.0   90,000,000.0
10                           NIGHT OF THE LIVING DEAD  Not Rated    96.0        7.8        89         1968   30,087,064   12,087,064.0   18,000,000.0
11                           NIGHT OF THE LIVING DEAD  Not Rated    96.0        7.8        89         1990    5,835,247    5,835,247.0            nan
12                     INVASION OF THE BODY SNATCHERS   Approved    80.0        7.7        92         1956        2,044            nan        2,044.0
13                                       EVIL DEAD II          R    84.0        7.7        72         1987    5,927,557    5,923,044.0        4,513.0
14                     INVASION OF THE BODY SNATCHERS   Approved    80.0        7.7        92         1978   24,946,533   24,946,533.0            nan
15                                          HALLOWEEN          R    91.0        7.7        87         1978   70,274,000   47,274,000.0   23,000,000.0
16                                  THE INVISIBLE MAN      TV-PG    71.0        7.6        87         1933          132            nan          132.0
17                                          THE BIRDS      PG-13   119.0        7.6        90         1963   11,436,929   11,403,529.0       33,400.0
18                                         THE OTHERS      PG-13   104.0        7.6        74         2001  207,765,056   96,522,687.0  111,242,369.0
19                                  THE INVISIBLE MAN      TV-PG    71.0        7.6        87         2020  139,011,965   64,914,050.0   74,097,915.0
20                                     THE WICKER MAN          R    88.0        7.5        87         1973      177,554       58,341.0      119,213.0
21                                      A QUIET PLACE      PG-13    90.0        7.5        82         2018  334,876,670  188,024,361.0  146,852,309.0
22                                      THE CONJURING          R   112.0        7.5        68         2013  317,740,900  137,400,141.0  180,340,759.0
23                                   28 DAYS LATER...          R   113.0        7.5        73         2003   82,955,633   45,064,915.0   37,890,718.0
24                     AN AMERICAN WEREWOLF IN LONDON          R    97.0        7.5        55         1981   61,968,388   31,973,249.0   29,995,139.0
25                                           THE OMEN          R   111.0        7.5        62         1976   48,577,431   48,570,885.0        6,546.0
26                       THE TEXAS CHAIN SAW MASSACRE          R    83.0        7.4        80         1986    8,025,872    8,025,872.0            na

MOVIES RANKED BY DOMESTIC BOX OFFICE

In [224]:
rankbybox = cleanmerge.sort_values(by=['Domestic'], ascending=False)
rankbybox.index = np.arange(1, len(rankbybox) + 1)
rankbybox = rankbybox[rankbybox['Domestic'] != 'nan']

In [228]:
rankbybox.dtypes

Title            object
Rating           object
Runtime          object
IMDB Score       object
Metascore        object
Release Year     object
Worldwide        object
Domestic         object
International    object
dtype: object

In [235]:
rankbybox['Domestic'] = rankbybox['Domestic'].astype(float)

ValueError: could not convert string to float: '96,761.0'